In [113]:
import pandas as pd 
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import os

In [114]:
acc = pd.read_csv('cleaned_data/acc.csv')
acc

timestamp_trunc Subject       Exam        AX        AY         AZ  \
0       2018-10-13 09:00:00      S1  Midterm 1 -4.191284  4.287085  -1.896855   
1       2018-10-13 09:00:00     S10  Midterm 1 -6.490503 -1.403481  -2.481240   
2       2018-10-13 09:00:00      S2  Midterm 1  5.240303 -0.134121  -3.103945   
3       2018-10-13 09:00:00      S3  Midterm 1 -6.437813  3.051255  -3.353027   
4       2018-10-13 09:00:00      S4  Midterm 1 -8.593330 -0.474214  -4.828359   
...                     ...     ...        ...       ...       ...        ...   
379712  2018-12-05 17:39:12      S3      Final -8.741821  4.454736  -9.570498   
379713  2018-12-05 17:39:13      S3      Final -9.872271  2.241738 -10.552456   
379714  2018-12-05 17:39:14      S3      Final -8.698711 -3.027305 -13.143867   
379715  2018-12-05 17:39:15      S3      Final -8.933423 -3.319497 -12.693604   
379716  2018-12-05 17:39:16      S3      Final -8.890313 -3.142266 -12.722344   

        magnitude_detrended  
0                  6.288404  
1                  7.088931  
2                  6.092064  
3                  7.873905  
4                  9.868295  
...                     ...  
379712            13.706150  
379713            14.623319  
379714            16.049716  
379715            15.873017  
379716            15.835704  

[379717 rows x 7 columns]

In [115]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from scipy.ndimage import gaussian_filter1d

# 1) Filter & parse time
midterm_df = acc[acc['Exam'] == 'Midterm 1'].copy()
midterm_df['timestamp_trunc'] = pd.to_datetime(midterm_df['timestamp_trunc'])

# 2) Sort data
midterm_df = midterm_df.sort_values(['Subject', 'timestamp_trunc'])

# 3) Estimate sample rate from timestamps
sampling_intervals = midterm_df['timestamp_trunc'].diff().dt.total_seconds()
sample_rate = 1 / sampling_intervals.median()

# 4) Apply Gaussian smoothing per student
midterm_df['magnitude_smooth'] = (
    midterm_df
    .groupby('Subject')['magnitude_detrended']
    .transform(lambda x: gaussian_filter1d(x.values, sigma=50))
)

# 5) Define fidget detection function (with index fix)
def detect_fidgets(accel_series, timestamps, window_size=20, spike_threshold=6.0, 
                   min_duration=1.0, max_duration=3.0, sample_rate=10):
    """
    Detect fidgets from detrended acceleration magnitude.

    Parameters:
    - accel_series (array-like): Detrended magnitude (m/s²) over time
    - timestamps (array-like): Time values corresponding to the accel_series
    - window_size (int): Rolling mean window in seconds
    - spike_threshold (float): Threshold above mean to detect spikes (in m/s²)
    - min_duration (float): Minimum fidget duration in seconds
    - max_duration (float): Maximum fidget duration in seconds
    - sample_rate (float): Samples per second (Hz)

    Returns:
    - fidget_events: List of (start_time, end_time, peak_value) tuples
    """
    # Ensure positional indexing
    accel = pd.Series(accel_series).reset_index(drop=True)
    timestamps = pd.Series(timestamps).reset_index(drop=True)
    rolling_mean = accel.rolling(window=int(window_size * sample_rate), min_periods=1).mean()
    above_thresh = accel > (rolling_mean + spike_threshold)

    fidget_events = []
    in_fidget = False
    start_idx = None

    for i, is_spike in enumerate(above_thresh):
        if is_spike and not in_fidget:
            in_fidget = True
            start_idx = i
        elif not is_spike and in_fidget:
            in_fidget = False
            end_idx = i
            duration = (end_idx - start_idx) / sample_rate
            if min_duration <= duration <= max_duration:
                fidget_events.append({
                    'start_time': timestamps[start_idx],
                    'end_time': timestamps[end_idx - 1],
                    'peak_value': max(accel[start_idx:end_idx])
                })

    return fidget_events

# 6) Detect fidgets per student
fidgets_list = []
for subject in midterm_df['Subject'].unique():
    sub_df = midterm_df[midterm_df['Subject'] == subject]
    fidgets = detect_fidgets(
        accel_series=sub_df['magnitude_detrended'],
        timestamps=sub_df['timestamp_trunc'],
        sample_rate=sample_rate
    )
    for f in fidgets:
        f['Subject'] = subject
        fidgets_list.append(f)

fidgets_df = pd.DataFrame(fidgets_list)

# 7) Plot smoothed time series
fig = px.line(
    midterm_df,
    x='timestamp_trunc',
    y='magnitude_smooth',
    color='Subject',
    title='Gaussian‐Smoothed Detrended Motion Magnitude – Midterm 1',
    labels={
        'timestamp_trunc': 'Time',
        'magnitude_smooth': 'Smoothed Detrended Magnitude (m/s²)'
    }
)

# 8) Add fidget markers
for subject in fidgets_df['Subject'].unique():
    sub_fidgets = fidgets_df[fidgets_df['Subject'] == subject]
    fig.add_trace(go.Scatter(
        x=sub_fidgets['start_time'],
        y=sub_fidgets['peak_value'],
        mode='markers',
        marker=dict(size=6, symbol='x', line=dict(width=1)),
        name=f'{subject} Fidgets',
        showlegend=True
    ))

fig.update_layout(
    legend_title='Student',
    hovermode='x unified',
    height=600
)

fig.show()


In [59]:
midterm_df

timestamp_trunc Subject       Exam        AX        AY        AZ  \
0     2018-10-13 09:00:00      S1  Midterm 1 -4.191284  4.287085 -1.896855   
10    2018-10-13 09:00:01      S1  Midterm 1 -4.191284  4.277505 -1.892065   
20    2018-10-13 09:00:02      S1  Midterm 1 -4.167334  4.277505 -1.882485   
30    2018-10-13 09:00:03      S1  Midterm 1 -4.157754  4.277505 -1.877695   
40    2018-10-13 09:00:04      S1  Midterm 1 -4.052373  4.301455 -1.848955   
...                   ...     ...        ...       ...       ...       ...   
79486 2018-10-13 11:27:22      S9  Midterm 1  0.148491  3.836821 -0.958008   
79487 2018-10-13 11:27:23      S9  Midterm 1 -0.790356  2.830913 -0.570015   
79488 2018-10-13 11:27:24      S9  Midterm 1 -1.140029  2.222578 -0.402363   
79489 2018-10-13 11:27:25      S9  Midterm 1 -3.764971  1.887275 -0.866997   
79490 2018-10-13 11:27:26      S9  Midterm 1 -5.415938  0.417266 -1.524297   

       magnitude_detrended  magnitude_smooth  
0                 6.288404          8.713852  
10                6.280432          8.713838  
20                6.261587          8.713825  
30                6.253775          8.713811  
40                6.192163          8.713784  
...                    ...               ...  
79486             3.957401         12.095916  
79487             2.993935         12.095665  
79488             2.530102         12.095477  
79489             4.299825         12.095351  
79490             5.641806         12.095289  

[79491 rows x 8 columns]

In [124]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from scipy.ndimage import gaussian_filter1d

# 1) Filter & parse time
midterm_df = acc[acc['Exam'] == 'Midterm 1'].copy()
midterm_df['timestamp_trunc'] = pd.to_datetime(midterm_df['timestamp_trunc'])

# 2) Sort data
midterm_df = midterm_df.sort_values(['Subject', 'timestamp_trunc'])

# 3) Estimate sample rate
sampling_intervals = midterm_df['timestamp_trunc'].diff().dt.total_seconds()
sample_rate = 1 / sampling_intervals.median()

# 4) Apply Gaussian smoothing per student
midterm_df['magnitude_smooth'] = (
    midterm_df
    .groupby('Subject')['magnitude_detrended']
    .transform(lambda x: gaussian_filter1d(x.values, sigma=40))
)

# 5) Define fidget detection function
def detect_fidgets(accel_series, timestamps, window_size=10, spike_threshold=4.0, 
                   min_duration=1.0, max_duration=4.0, sample_rate=10):
    """
    Detect fidgets from detrended acceleration magnitude.

    Parameters:
    - accel_series (array-like): Detrended magnitude (m/s²) over time
    - timestamps (array-like): Time values corresponding to the accel_series
    - window_size (int): Rolling mean window in seconds
    - spike_threshold (float): Threshold above mean to detect spikes (in m/s²)
    - min_duration (float): Minimum fidget duration in seconds
    - max_duration (float): Maximum fidget duration in seconds
    - sample_rate (float): Samples per second (Hz)

    Returns:
    - fidget_events: List of (start_time, end_time, peak_value) tuples
    """
    # Ensure positional indexing
    accel = pd.Series(accel_series).reset_index(drop=True)
    timestamps = pd.Series(timestamps).reset_index(drop=True)
    rolling_mean = accel.rolling(window=int(window_size * sample_rate), min_periods=1).mean()
    above_thresh = accel > (rolling_mean + spike_threshold)

    fidget_events = []
    in_fidget = False
    start_idx = None

    for i, is_spike in enumerate(above_thresh):
        if is_spike and not in_fidget:
            in_fidget = True
            start_idx = i
        elif not is_spike and in_fidget:
            in_fidget = False
            end_idx = i
            duration = (end_idx - start_idx) / sample_rate
            if min_duration <= duration <= max_duration:
                fidget_events.append({
                    'start_time': timestamps[start_idx],
                    'end_time': timestamps[end_idx - 1],
                    'peak_value': max(accel[start_idx:end_idx])
                })

    return fidget_events

# 6) Detect fidgets per student
fidgets_list = []
for subject in midterm_df['Subject'].unique():
    sub_df = midterm_df[midterm_df['Subject'] == subject]
    fidgets = detect_fidgets(
        accel_series=sub_df['magnitude_detrended'],
        timestamps=sub_df['timestamp_trunc'],
        sample_rate=sample_rate
    )
    for f in fidgets:
        f['Subject'] = subject
        fidgets_list.append(f)

fidgets_df = pd.DataFrame(fidgets_list)

# 7) Project fidget points onto the smoothed graph
fidgets_df['smoothed_value'] = fidgets_df.apply(
    lambda row: midterm_df[
        (midterm_df['Subject'] == row['Subject']) &
        (midterm_df['timestamp_trunc'] == row['start_time'])
    ]['magnitude_smooth'].values[0] if not midterm_df[
        (midterm_df['Subject'] == row['Subject']) &
        (midterm_df['timestamp_trunc'] == row['start_time'])
    ].empty else None,
    axis=1
)

# 8) Plot smoothed time series
fig = px.line(
    midterm_df,
    x='timestamp_trunc',
    y='magnitude_smooth',
    color='Subject',
    title='Gaussian‐Smoothed Detrended Motion Magnitude – Midterm 1',
    labels={
        'timestamp_trunc': 'Time',
        'magnitude_smooth': 'Smoothed Detrended Magnitude (m/s²)'
    }
)

# 9) Add fidget markers projected onto smoothed line
for subject in fidgets_df['Subject'].unique():
    sub_fidgets = fidgets_df[fidgets_df['Subject'] == subject]
    fig.add_trace(go.Scatter(
        x=sub_fidgets['start_time'],
        y=sub_fidgets['smoothed_value'],
        mode='markers',
        marker=dict(size=6, symbol='x', line=dict(width=1)),
        name=f'{subject} Fidgets',
        showlegend=True
    ))

fig.update_layout(
    legend_title='Student',
    hovermode='x unified',
    height=600
)

fig.show()
